In [1]:
from msclap import CLAP
import laion_clap
import pandas as pd
import torch
import librosa
import IPython.display as ipd
from experiments.utils.set_torch_device import set_torch_device

ModuleNotFoundError: No module named 'experiments'

In [ ]:
# Load models
msclap_model = CLAP(version = '2023', use_cuda=True) # version can be 2022 or 2023
laion_clap_model = laion_clap.CLAP_Module(enable_fusion=False)
laion_clap_model.load_ckpt()

Load our best checkpoint in the paper.
The checkpoint is already downloaded
Load Checkpoint...
logit_scale_a 	 Loaded
logit_scale_t 	 Loaded
audio_branch.spectrogram_extractor.stft.conv_real.weight 	 Loaded
audio_branch.spectrogram_extractor.stft.conv_imag.weight 	 Loaded
audio_branch.logmel_extractor.melW 	 Loaded
audio_branch.bn0.weight 	 Loaded
audio_branch.bn0.bias 	 Loaded
audio_branch.patch_embed.proj.weight 	 Loaded
audio_branch.patch_embed.proj.bias 	 Loaded
audio_branch.patch_embed.norm.weight 	 Loaded
audio_branch.patch_embed.norm.bias 	 Loaded
audio_branch.layers.0.blocks.0.norm1.weight 	 Loaded
audio_branch.layers.0.blocks.0.norm1.bias 	 Loaded
audio_branch.layers.0.blocks.0.attn.relative_position_bias_table 	 Loaded
audio_branch.layers.0.blocks.0.attn.qkv.weight 	 Loaded
audio_branch.layers.0.blocks.0.attn.qkv.bias 	 Loaded
audio_branch.layers.0.blocks.0.attn.proj.weight 	 Loaded
audio_branch.layers.0.blocks.0.attn.proj.bias 	 Loaded
audio_branch.layers.0.blocks.0.norm2.we

In [5]:
audio_embeddings_path = "D:/datasets/soundly_embeddings.csv"
df = pd.read_csv(audio_embeddings_path, index_col=0)
audio_embeddings = torch.load("D:/datasets/soundly_embeddings.pt")

In [ ]:
# Utils and Helpers
device, device_name = set_torch_device()
print(f"Torch device set to: {device_name}\n")

# Load dataset paths
with open ('experiments/configs/kfold17-zero_shot.json', 'r') as f:
    settings = json.load (f)

data = pd.read_csv(settings['dataset_drive'] + settings['dataset_path'])
data = data[data['category'] != 'other'] # Filter out sounds without without a category.
data.reset_index(drop=True)

In [5]:
def semantic_search(prompt:str, n_return:int=10, audio_embeddings=None):
    """
    Given a prompt, return audio files with the most similar semantic similarity. Based on LAION CLAP and MSCLAP.

    To do: shorten search time by limiting searches to the most likely category. Currently: 6.2 sec.

    Args.
    - prompt: A string containing the entire search query.
    - n_return: How many files the query should return.
    - audio_embeddings: The audio embeddings to compare with.
    """

    if (audio_embeddings == None): 
        print("Please provide a list of audio embeddings.")
        return
    
    # Extract text embeddings
    text_data = ["", prompt] # CLAP has a bug where two text prompts are required. Discard the first.
    text_embedding = laion_clap_model.get_text_embedding(text_data)[1]

    # Calculate text-audio similarity
    cos = torch.nn.CosineSimilarity(dim=1, eps=1e-08)

    similarities = torch.tensor([cos(embedding.clone().detach(), torch.tensor(text_embedding).clone().detach()) for embedding in audio_embeddings])
    print(similarities)
    idx = torch.argsort(similarities, dim=0, descending=True)

    return idx[:n_return]

# Retrieve k 

idx = semantic_search("harsh wind", n_return=10, audio_embeddings=audio_embeddings)
similarity_sorted_files = df.iloc[idx]

tensor([-0.0666, -0.0575,  0.0061,  ...,  0.0061,  0.0061,  0.0061])


In [8]:
path = similarity_sorted_files['path'].iloc[0]
# Change drive:
path = path.replace("E:", "D:")
audio, sr = librosa.load(path, sr=similarity_sorted_files['sample_rate'].iloc[0])
print(path)
ipd.Audio(audio, rate=sr)

D:/Soundly Library juni 2023/Soundly Pro/Food & Drink/Cooking/Food & Drink, Cooking, Bacon, Frying 01.wav
